## Load Required Packages and Data

In [1]:
from __future__ import absolute_import
from __future__ import print_function
from __future__ import division

import json, os, re, shutil, sys, time
from importlib import reload
import collections, itertools
import unittest
from IPython.display import display, HTML

from cytoolz import concatv

# NLTK for NLP utils and corpora
import nltk,pprint
from nltk import word_tokenize
nltk.download('treebank')
nltk.download('punkt')

# NumPy and TensorFlow
import numpy as np
import pandas as pd
import tensorflow as tf
print(tf.__version__)

[nltk_data] Downloading package treebank to
[nltk_data]     /home/huyue012/nltk_data...
[nltk_data]   Package treebank is already up-to-date!
[nltk_data] Downloading package punkt to /home/huyue012/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


/home/huyue012/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [3]:
# Helper libraries
from w266_common import utils, vocabulary, tf_embed_viz

# model
import rnnlm; reload(rnnlm)

<module 'rnnlm' from '/home/huyue012/W266TextSummarization/rnnlm.py'>

### read nyt flat file

In [4]:
# use Alan's way of loading files
import pandas as pd
nyt_data = pd.read_csv('nyt_structured_data.csv.1000', 
                       delimiter=',', index_col=0, header=None, quotechar='"', quoting=1, 
                       skipinitialspace=True, engine='c')

In [5]:
nyt_data.head(2)

1  \
0                                                                                     
original/2007/06/15/1854648.xml   Often Accused, Never Charged, Newark's Ex-Mayo...   
original/2007/06/15/1854649.xml   An Earsplitting Symphony, With the Maestro in ...   

                                                                                  2  \
0                                                                                     
original/2007/06/15/1854648.xml   When federal prosecutors found in 1995 that Sh...   
original/2007/06/15/1854649.xml   There is the yelp, an electronic yodel that gr...   

                                                                                  3  
0                                                                                    
original/2007/06/15/1854648.xml   When federal prosecutors found in 1995 that Sh...  
original/2007/06/15/1854649.xml   There is the yelp, an electronic yodel that gr...

### Tokenize and Sentence segmentation

In [7]:
# # tokenize built in load_data function
from nltk import word_tokenize
from nltk.tokenize import sent_tokenize, word_tokenize
import nltk
import string

def sent_tokenize_rm_punct (blob):
    bexp = ''    
    for i, char in (enumerate(blob)):
        next_cap = False
        prev_lower = False
        
        
        if char in string.punctuation :
            if char in '.?!' :

                if i+1 >= len(blob):
                    next_cap = False
                else:
                    next_cap = blob[i+1].isupper()

                if i-1 <0:
                    prev_lower = False
                else:
                    prev_lower = blob[i-1].islower()

                if next_cap and prev_lower : 
                    bexp = bexp + char + '  '
                else:
                    bexp = bexp + char
            else :
                bexp = bexp + ' '
        else :
            if char.isnumeric() : 
                bexp = bexp + 'N'
            else :
                bexp = bexp + char.lower()
    
    return(sent_tokenize(bexp))

# a list of list
body_tokens = [] 
title_tokens = []

for s in range(len(nyt_data)):
    #print(nyt_data[3][s])
    body_token = sent_tokenize_rm_punct(nyt_data[3][s])
    body_tokens.append(body_token)
    
    title_token = sent_tokenize_rm_punct(nyt_data[1][s])
    title_tokens.append(title_token)
    #for j in range(len(body_token)) :
    #    print(j,"<s>",body_token[j],"</s>")

    
for i in range(len(body_tokens)):
    for j in range(len(body_tokens[i])) :
        print(i,j,"<s>",body_tokens[i][j],"</s>")


0 0 <s> when federal prosecutors found in NNNN that sharpe james  then the mayor of newark  could not account for hundreds of thousands of dollars in donations from political patrons  his only penalty was a  NN NNN fine from the state election commission. </s>
0 1 <s> two years later  mr. james s chief of staff was imprisoned for accepting bribes from city contractors. </s>
0 2 <s> the mayor praised him as   a loyal public servant   and escaped from that investigation unscathed  soon winning a second public office as state senator. </s>
0 3 <s> and throughout his five terms at the helm of new jersey s largest city  mr. james lived a lifestyle so lavish    complete with a beach house  NN foot yacht and rolls royce    that he was frequently the focus of accusations and insinuations  but he never faced a criminal charge. </s>
0 4 <s> now mr. james  who left office last summer after NN years at newark city hall  has been told by federal prosecutors that he is likely to face indictment on c

17 2 <s> in didier massard s work  nature really is fake. </s>
17 3 <s> mr. massard fabricates models in his paris studio and photographs them  without subsequent digital manipulation. </s>
17 4 <s> past show titles    artificial paradise      imaginary journeys    made the fakery explicit  but here mr. massard moves somewhat away from that and considers   territories    geographical rather than politically defined ones .a mountain towers over a craggy field of blue white ice in   glacier    trees with pruned branches are set amid a gray wetland in   the marsh    a rock arch frames a total eclipse of the sun in   the grotto    and   november   is a gorgeous  double exposed image of trees caught in an early season snowstorm. </s>
17 5 <s> beautiful and classically    in the NNth century sense    romantic  mr. massard s photographs can also feel at times overly mannered and precious. </s>
17 6 <s> he is a virtuoso image maker  but prone to the kind of na  xef f  wide eyed wonder that s b

44 56 <s> looking at the c.t.e. </s>
44 57 <s> tangles on a computer screen on wednesday  she said they would be   a piece of the puzzle   she is eager to complete for herself and perhaps others. </s>
44 58 <s> i m interested for me and for other mothers    she said. </s>
44 59 <s> if some good can come of this  that s it. </s>
44 60 <s> maybe some young football player out there will see this and be saved the trouble. </s>
44 61 <s> pro footballcorrection  june NN  NNNN  saturday a sports article yesterday about justin strzelczyk  a former national football league player who was found post mortem to have had early signs of brain damage that experts said was most likely caused by football concussions  misidentified the medical institution where bennet omalu  the doctor who made the diagnosis  is a clinical instructor of neuropathology. </s>
44 62 <s> it is the university of pittsburgh school of medicine  not the university of pittsburgh medical center. </s>
45 0 <s> on a century old go

51 7 <s> on most holes  montgomerie walked with his head down  a few paces ahead of goddard  his playing partners tim clark and chris dimarco  and their caddies. </s>
51 8 <s> he started well  with a birdie on his first hole  the par N NNth. </s>
51 9 <s> after stringing together six pars  montgomerie made a bogey on no. </s>
51 10 <s> NN when his drive found the second cut of rough and he put his second shot into a deep greenside bunker    he kicked the divot he left in disgust    chipped out and two putted for a N.montgomerie hit N of NN fairways and needed NN putts. </s>
51 11 <s> he s been good to deal with    goddard said. </s>
51 12 <s> he didn t play too good today  obviously. </s>
51 13 <s> he hit a couple bad shots and it really cost him. </s>
51 14 <s> but he got over it. </s>
51 15 <s> snedeker has fast start    brandt snedeker won the united states amateur public links championship in NNNN. </s>
51 16 <s> that same year  michelle wie won the women s version of the event. </

73 27 <s> the news release  which reads as if it were written by a world wrestling entertainment personality after a particularly grueling match  carries the news that vince mcmahon  the w.w.e. </s>
73 28 <s> chairman  had been blown up in his limousine in wilkes barre  pa.  after a w.w.e. </s>
73 29 <s> event. </s>
73 30 <s> it asks    how could mr. mcmahon have survived the fiery explosion? </s>
73 31 <s> it then states that mr. mcmahon   is presumed dead. </s>
73 32 <s> an official investigation   is under way  according to the statement. </s>
73 33 <s> of course  it was all a hoax  and few mainstream news organizations gave it any attention. </s>
73 34 <s> one exception was the times leader in wilkes barre  which published an article letting local residents know that the   bombing    which was staged and televised on the usa network  was a stunt  timesleader.com .dan mitchellwhat s online </s>
74 0 <s> i hunkered over a six burner commercial stove  my pulse pounding and my hands dr

...

949 20 <s> seat width is typically the distance between armrests on a seat or waist area  more and more airlines taper the width toward the legs  an adjustment their research shows provides more comfort during sleep. </s>
949 21 <s> a web site that evaluates seats  called flatseats.com  lists seat pitches for about NNN airlines worldwide. </s>
949 22 <s> in one of the toughest head to head seat skirmishes  virgin atlantic airways and british airways have sidestepped the legroom problem in their top class by positioning the seats so they angle toward the aisle in a herringbone pattern. </s>
949 23 <s> virgin atlantic s head to toe seat length is NN.N inches  it has only upper class seating   british airways  is NN inches in business class and NN inches in first class. </s>
949 24 <s> in width  virgin offers NN inches  and british air measures NN.NN at the waist. </s>
949 25 <s> while flat bed seats recline NNN degrees  the bed is not parallel to the floor  leaving the passenger s head h

958 3 <s> we are almost married. </s>
958 4 <s> the reason for mr. gallois  charm offensive? </s>
958 5 <s> the troubled european aerospace and military giant wants to land a  NN billion contract to provide NNN aerial refueling tankers to the united states air force. </s>
958 6 <s> it is one of the biggest pentagon contracts in decades  and eads is counting on the political clout of alabama officials  who are hoping to get an airbus factory in their state  to help the company in washington. </s>
958 7 <s> it is not easy being a foreign company seeking more pentagon business  especially when the competition is the archrival boeing  america s second largest military supplier and a skilled washington hand. </s>
958 8 <s> yet to eads  expanding its military activities in the united states is increasingly important  especially since last year s profits in its military and space business were nearly offset by losses in its troubled airbus commercial aviation division. </s>
958 9 <s> to have 

967 37 <s> when he descends to fetch her back  eurydice faces a painful choice  to re enter the world above  where imperfect human love and the potential for pain awaits  or remain below where she is beyond its reach? </s>
967 38 <s> either choice involves risk and loss. </s>
967 39 <s> mr. waters and his design collaborators have framed ms. ruhl s play with uncommon sensitivity and stylistic sympathy. </s>
967 40 <s> in a less felicitous production  i can imagine the play cloying into preciousness. </s>
967 41 <s> scott bradley s tilted vision of the underworld as a slightly dilapidated spa  wallpapered in letters written from the dead to the living  perfectly matches the writing s off kilter tone. </s>
967 42 <s> the shimmery  dank lighting by russell h. champa echoes the quicksilver changes in tenor. </s>
967 43 <s> and the selection of music likewise parallels the emotional currents without overwhelming the breezy playfulness of the dialogue. </s>
967 44 <s> arvo p  xeN rt s haunti

978 5 <s> lola wasserstein gave wendy ample advice  which she eagerly passed on    always look nice when you throw out the garbage. </s>
978 6 <s> you never know who you might meet. </s>
978 7 <s> lola schleiffer was born in a village in poland in NNNN  immigrated with her family to new jersey in NNNN  then moved to brooklyn and the upper east side. </s>
978 8 <s> she married morris wasserstein  an inventor and businessman who died in NNNN.their daughter sandra w. meyer  a prominent marketing executive  died in NNNN. </s>
978 9 <s> wendy wasserstein died last year. </s>
978 10 <s> mrs. wasserstein is survived by her daughter georgette levis  owner of an inn in vermont  and her son  bruce wasserstein  a wall street magnate who helped lead protests against removing the nest of two red tailed hawks from a cornice of his fifth avenue co op apartment building. </s>
978 11 <s> the female hawk was named lola. </s>
978 12 <s> mrs. wasserstein is also survived by NN grandchildren and six great 

987 45 <s> in the NNNNs  yitzhak rabin  the soldier who had led its army into acquisition of the west bank and gaza in the six day war of NNNN  told his people that it was time to partition the land and to accept palestinian sovereignty. </s>
987 46 <s> it was an unsentimental peace  to   get gaza out of tel aviv    as mr. rabin put it  but it was peace nonetheless. </s>
987 47 <s> in varying degrees  all of mr. rabin s successors accepted this legacy. </s>
987 48 <s> there was even a current in israel possessed of a deep curiosity about the palestinians  a romance of sorts about their ways and folk culture and their connection to the sacred land. </s>
987 49 <s> all this is stilled. </s>
987 50 <s> palestinian society has now gone where no   peace processors   or romantic poets dare tread. </s>
987 51 <s> op ed contributorfouad ajami  a professor at the johns hopkins school of advanced international studies  is the author of   the foreigner s gift  the americans  the arabs and the ira

In [22]:
# import sent_segment
# len(body_tokens)
# # body_tokens[999]

# sentences = []
# for t in range(len(body_tokens)):
#     sentence = np.array(sent_segment.segment_sentences(body_tokens[t]))
#     sentences.append(sentence)
# # sentence[:5]

### Further Preprocessing
leverage w266_common module
tokenize --> canonicalize digit --> canonicalize word --> vocabuluary --> split

In [6]:
# Helper libraries
# assuming body and title are in different arrays, but split training/test not random or shuffled

reload(utils)
V = 10000
# lower case, DG, Unknown, pad sentense start/end, convert to id, split into training and test data sets
vocab, train_x_ids, test_x_ids, train_y_ids, test_y_ids = utils.load_data(nyt_data[3][:], nyt_data[1][:], split=0.8, V=V, shuffle=42)

train_x_ids[10:20]

[nltk_data] Downloading package treebank to
[nltk_data]     /home/huyue012/nltk_data...
[nltk_data]   Package treebank is already up-to-date!
Vocabulary: 10,000 types
Loaded 1,000 documents (24316 sentences)
Training set: 800 documents (20,178 sentences)
Test set: 200 documents (4,138 sentences)


[array([  0,  65, 888, ...,   0,   5,   0], dtype=int32),
 array([  0,  65, 888, ...,   0,   5,   0], dtype=int32),
 array([  0, 201,   6, ...,   0,   5,   0], dtype=int32),
 array([  0, 306, 446, ..., 694, 201,   0], dtype=int32),
 array([   0,  234, 2129, ...,   65,  888,    0], dtype=int32),
 array([  0,  16, 832, ...,  65, 888,   0], dtype=int32),
 array([  0,  65,   6, ...,  65, 888,   0], dtype=int32),
 array([  0,  65, 234, ..., 234, 358,   0], dtype=int32),
 array([  0,   6, 358, ..., 234, 358,   0], dtype=int32),
 array([  0, 256,   6, ..., 168, 998,   0], dtype=int32)]

In [21]:
# check length of train and test sets
print(len(train_x_ids),len(train_y_ids))
print(len(test_x_ids),len(test_y_ids))

800 800
200 200


In [20]:
symbol=['<GO>','</s>','<s>','<unk>']
[{s:vocab.word_to_id[s]} for s in symbol[1:]]

[{'</s>': 1}, {'<s>': 0}, {'<unk>': 2}]

In [19]:
# vocab.word_to_id["<GO>"]
print(vocab.START_TOKEN, vocab.END_TOKEN,vocab.UNK_TOKEN)

<s> </s> <unk>


## Embedding

### Sentence Embedding
For extractive modeling - sentence ranking

In [5]:
# # !pip install tensorflow_hub
# import tensorflow as tf
# import tensorflow_hub as hub
# embed = hub.Module("https://tfhub.dev/google/universal-sentence-encoder/2")
# embeddings = embed([
# "The quick brown fox jumps over the lazy dog.",
# "I am a sentence for which I would like to get its embedding"])
# session=tf.Session()
# session.run([tf.global_variables_initializer(), tf.tables_initializer()])
# print (tf.Session().run(embeddings))

## Build Core Graph

H : hidden state size = embedding size = per-cell output size

May need to update that

## Build Train Graph

## Trainint The Model

In [34]:
def run_epoch(lm, session, batch_iterator,
              train=False, verbose=False,
              tick_s=10, learning_rate=None):
    assert(learning_rate is not None)
    start_time = time.time()
    tick_time = start_time  # for showing status
    total_cost = 0.0  # total cost, summed over all words
    total_batches = 0
    total_words = 0

    if train:
        train_op = lm.train_step_
        use_dropout = True
        loss = lm.train_loss_
    else:
        train_op = tf.no_op()
        use_dropout = False  # no dropout at test time
        loss = lm.loss_  # true loss, if train_loss is an approximation
        
    for i, (en_in, de_in, de_out) in enumerate(batch_iterator):
        
        # At first batch in epoch, get a clean intitial state.
        if i == 0:
            pass
            h = session.run(lm.encoder_initial_h_, {lm.encoder_inputs_: en_in})

        feed_dict = {
            lm.encoder_inputs_: en_in,
            lm.decoder_outputs_: de_out,
            lm.decoder_inputs_: de_in,
            lm.encoder_initial_h_: h,
            lm.learning_rate_: learning_rate,
            lm.use_dropout_: use_dropout
        }
        ops = [loss, self.encoder_final_h_, train_op] # do i need self.encoder_final_h or decoder??  
   
        cost = 0.0
        vals = session.run(ops, feed_dict)
        cost = vals[0] #loss
        h = vals[1] #final_h

        total_cost += cost
        total_batches = i + 1
        total_words += w.size  # w.size = batch_size * max_time


        # Print average loss-so-far for epoch
        # If using train_loss_, this may be an underestimate.
        if verbose and (time.time() - tick_time >= tick_s):
            avg_cost = total_cost / total_batches
            avg_wps = total_words / (time.time() - start_time)
            print("[batch {:d}]: seen {:d} words at {:.1f} wps, loss = {:.3f}".format(
                i, total_words, avg_wps, avg_cost))
            tick_time = time.time()  # reset time ticker

    return total_cost / total_batches

In [35]:
def score_dataset(lm, session, x_ids, y_ids, name="Data"):
    # For scoring, we can use larger batches to speed things up.
    bi = utils.rnnlm_batch_generator(x_ids,y_ids, batch_size=batch_size)
    cost = run_epoch(lm, session, bi, 
                     learning_rate=0.0, train=False, 
                     verbose=False, tick_s=3600)
    print("{:s}: avg. loss: {:.03f}  (perplexity: {:.02f})".format(name, cost, np.exp(cost)))
    return cost

In [36]:
# Training parameters
# max_encoder_time = 25
# max_decoder_time = 25
batch_size = 100
learning_rate = 0.01 #default 0.01
num_epochs = 2

# flattern the list first, then for each x or y, it's a list of ids 
# which covers several sentences, not a list of list
# shall i use raw sentences input or the id to get len(), shall i include start/end token??
    # max length of x_i, total # of tokens for x_i
max_source_length = max([len(s) for s in train_x_ids])
    # max length of y_i, total # of tokens for y_i
max_target_length = max([len(s) for s in train_y_ids])


# Model parameters
model_params = dict(V=vocab.size, 
                    H=200, 
                    softmax_ns=100,
                    num_layers=3, 
                    batch_size=batch_size)

TF_SAVEDIR = "/tmp/w266/project"
checkpoint_filename = os.path.join(TF_SAVEDIR, "rnnlm")
trained_filename = os.path.join(TF_SAVEDIR, "rnnlm_trained")

In [37]:
# Will print status every this many seconds
import rnnlm; reload(rnnlm)
print_interval = 5

lm = rnnlm.RNNLM(**model_params)
lm.BuildCoreGraph()
lm.BuildTrainGraph()

In [38]:
reload(utils)

# Explicitly add global initializer and variable saver to LM graph
with lm.graph.as_default():
    initializer = tf.global_variables_initializer()
    saver = tf.train.Saver()
    
# Clear old log directory
shutil.rmtree(TF_SAVEDIR, ignore_errors=True)
if not os.path.isdir(TF_SAVEDIR):
    os.makedirs(TF_SAVEDIR)

with tf.Session(graph=lm.graph) as session:
    # Seed RNG for repeatability
    tf.set_random_seed(42)

    session.run(initializer)

    for epoch in range(1,num_epochs+1):
        t0_epoch = time.time()
        bi = utils.rnnlm_batch_generator(train_x_ids, train_y_ids, batch_size)
        print("[epoch {:d}] Starting epoch {:d}".format(epoch, epoch))
        print(batch_size)

        # Run a training epoch.    
        cost = run_epoch(lm, session, bi, 
                 learning_rate=learning_rate, train=True, 
                 verbose=True, tick_s=10)
        print("loss: {:.03f}  (perplexity: {:.02f})".format(cost, np.exp(cost)))

        print("[epoch {:d}] Completed in {:s}".format(epoch, utils.pretty_timedelta(since=t0_epoch)))
    
        # Save a checkpoint
        saver.save(session, checkpoint_filename, global_step=epoch)
    
        ##
        # score_dataset will run a forward pass over the entire dataset
        # and report perplexity scores. This can be slow (around 1/2 to 
        # 1/4 as long as a full epoch), so you may want to comment it out
        # to speed up training on a slow machine. Be sure to run it at the 
        # end to evaluate your score.
#         if epoch == num_epochs:
        print("[epoch {:d}]".format(epoch), end=" ")
        score_dataset(lm, session, train_ids, name="Train set")
        print("[epoch {:d}]".format(epoch), end=" ")
        score_dataset(lm, session, test_ids, name="Test set")
        print("")

    
    # Save final model
    saver.save(session, trained_filename)

[nltk_data] Downloading package treebank to
[nltk_data]     /home/huyue012/nltk_data...
[nltk_data]   Package treebank is already up-to-date!
[epoch 1] Starting epoch 1
100


ValueError: setting an array element with a sequence.

## Inference-WIP

In [ ]:
def sample_step(lm, session, input_w, initial_h):
    """Run a single RNN step and return sampled predictions.
  
    Args:
      lm : rnnlm.RNNLM
      session: tf.Session
      input_w : [batch_size] vector of indices
      initial_h : [batch_size, hidden_dims] initial state
    
    Returns:
      final_h : final hidden state, compatible with initial_h
      samples : [batch_size, 1] vector of indices
    """
    # Reshape input to column vector
    input_w = np.array(input_w, dtype=np.int32).reshape([-1,1])
  
    #### YOUR CODE HERE ####
    # Run sample ops
    samples = session.run(lm.pred_samples_, {lm.input_w_: input_w})
    final_h = session.run(lm.final_h_, {lm.input_w_: input_w})

        #### END(YOUR CODE) ####
        # Note indexing here: 
        #   [batch_size, max_time, 1] -> [batch_size, 1]
    return final_h, samples[:,-1,:]

In [ ]:
# Same as above, but as a batch
max_steps = 20
num_samples = 10
random_seed = 42

lm = rnnlm.RNNLM(**model_params)
lm.BuildCoreGraph()
lm.BuildSamplerGraph()

with lm.graph.as_default():
    saver = tf.train.Saver()

with tf.Session(graph=lm.graph) as session:
    # Seed RNG for repeatability
    tf.set_random_seed(random_seed)
    
    # Load the trained model
    saver.restore(session, trained_filename)

    # Make initial state for a batch with batch_size = num_samples
    w = np.repeat([[vocab.START_ID]], num_samples, axis=0)
    h = session.run(lm.initial_h_, {lm.input_w_: w})
    # We'll take one step for each sequence on each iteration 
    for i in range(max_steps):
        h, y = sample_step(lm, session, w[:,-1:], h)
        w = np.hstack((w,y))

    # Print generated sentences
    for row in w:
        for i, word_id in enumerate(row):
            print(vocab.id_to_word[word_id], end=" ")
            if (i != 0) and (word_id == vocab.START_ID):
                break
        print("")

## Score New Data - Placeholder

## Reference: NMT Tutorial
https://github.com/tensorflow/nmt

https://towardsdatascience.com/seq2seq-model-in-tensorflow-ec0c557e560f; https://github.com/deep-diver/EN-FR-MLT-tensorflow/blob/master/dlnd_language_translationv2.ipynb